#### Static Variables
Standard variables that are static throughout a run

In [1]:
import numpy as np 

## Populate all the radar variables required:
TIME_STEP = 0.241
WAVELENGTH = 0.01233714
RANGE_BIN_SIZE = 199.939e-3 # Range bin size (m)
MAX_DIST = 512 * RANGE_BIN_SIZE

f_0 = 24e9  # Center Frequency (Hz)
f_c = 24.500e9  # Center Frequency (Hz)
f_chirp = 4.14937759  # Chirp Sequence Frequency (Hz)
f_r = 750e6  # Ramp Frequency (Hz)
T_r = 0.241  # Duration of one cycle (s) - Chirp sequence
m_w = f_r / T_r  # Slope of the ramp (Hz/s)

f_s = 1 / TIME_STEP

# Generate SFC gain curve
range_vector = np.arange(512) * RANGE_BIN_SIZE
SFC_gain = range_vector ** 2

# CFAR Params
num_training_cells = 10
num_guard_cells = 4
threshold_factor = 3  # Adjust as needed for CFAR sensitivity

#### Load Data

In [2]:
import os
from radar.dataparsing.td_textdata_parser import read_columns
from scipy.fftpack import fft
from matplotlib import pyplot as plt

td_data = []

# Different Test Cases
# timeStampFolder = "2024-10-17_11-57-43.359" # Take-off (at least 4 drones)
# timeStampFolder = "2024-10-17_12-04-36.137" # Landing UAVs - for at least 2 UAVs
# timeStampFolder = "2024-10-17_15-59-35.092" # Up/Down Movement (for 5 UAVs)

# DJ Mini Tests - hovering overtop the radar tests, distances mentioned
# timeStampFolder = "2024-10-18_09-55-39.076 1.3m"
# timeStampFolder = "2024-10-18_09-59-12.941 5.0m"
timeStampFolder = "2024-10-18_10-02-03.580 15m"
#timeStampFolder = "2024-10-18_10-13-20.561 20m"
# timeStampFolder = "2024-10-18_10-10-43.904 29m"

directory_to_process = f"/data/radar/Oct17/{timeStampFolder}/TD"


# directory_to_process = f"output/2024-09-29_20-20-41/radar"

def process_data_from_folder(self):
        
        # List all files in the directory
        files = os.listdir(directory_to_process)
        
        # Filter the files based on the naming convention
        txt_files = [f for f in files if f.endswith('.txt')]
        
        # Sort the files if needed (optional)
        txt_files.sort()
        
        # Process each file one by one
        for file_name in txt_files:
            file_path = os.path.join(directory_to_process, file_name)
            new_fd_data = read_columns(file_path)
            td_data.append(new_fd_data.td_data)
        
            
process_data_from_folder(directory_to_process)
td_data = np.array(td_data)
I1_data = td_data[:, :, 0]  # Extract the I1 signal, which is the first column across all frames and range bins
Q1_data = td_data[:, :, 1]  # Extract the Q1 signal, which is the second column across all frames and range bins
I2_data = td_data[:, :, 2]  # Extract the I2 signal, which is the third column across all frames and range bins
Q2_data = td_data[:, :, 3]  # Extract the IQ2 signal, which is the fourth column across all frames and range bins
Rx1 = I1_data + 1j * Q1_data
Rx2 = I2_data + 1j * Q2_data

n_r = I1_data.shape[0] # number of total chirps - assumes all have the same shape, which they should
n_s = I1_data.shape[1] # number of samples - assumes all have the same shape, which they should
T_M = T_r * n_r  # Total measurement time (s)

SINGLE_TO_PROCESS = I1_data

print(f"Num samples: {td_data.shape[0]}")

Num samples: 382


#### Process and Plot the data

In [3]:
## Plots that will be used -- Polar and Cartesian plots
fig_polar, ax_polar = plt.subplots(subplot_kw={'projection': 'polar'}, figsize=(6, 6))
fig_cartesian, ax_cartesian = plt.subplots(figsize=(6, 6))

fig_polar.suptitle("Radar Detections - Polar Plot")
fig_cartesian.suptitle("Radar Signal - Cartesian Plot")

# Close the figures to prevent static images from being displayed statically (will be shown dynamically below)
plt.close(fig_polar)
plt.close(fig_cartesian)

In [4]:
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from plots.PlotFunctions import plot_polar_detections, plot_cartesian_detections
from radar.cfar import ca_cfar_detector, caso_cfar
from constants import DIST_BETWEEN_ANTENNAS, SPEED_LIGHT

# Calculate the angles
def calculate_angles(I1_fft, Q1_fft, I2_fft, Q2_fft):
    phase_diff_1 = np.angle(I1_fft * np.conj(I2_fft))
    phase_diff_2 = np.angle(Q1_fft * np.conj(Q2_fft))
    phase_diff = (phase_diff_1 + phase_diff_2) / 2
    sin_arg = (phase_diff * SPEED_LIGHT) / (2 * np.pi * DIST_BETWEEN_ANTENNAS * f_c)
    sin_arg = np.clip(sin_arg, -1, 1)  # Clip values to the valid range for arcsin
    angles = np.degrees(np.arcsin(sin_arg))
    return np.clip(angles, -90, 90)

def update(frame):
    # Clear each figure's axes for the new frame
    ax_polar.clear()
    ax_cartesian.clear()

    I1 = I1_data[frame]
    Q1 = Q1_data[frame]
    I2 = I2_data[frame]
    Q2 = Q2_data[frame]

    I1_fft = np.fft.fft(I1)[:512]
    Q1_fft = np.fft.fft(Q1)[:512]
    I2_fft = np.fft.fft(I2)[:512]
    Q2_fft = np.fft.fft(Q2)[:512]
    
    angles = calculate_angles(I1_fft, Q1_fft, I2_fft, Q2_fft)

    I1_fft *= SFC_gain
    Q1_fft *= SFC_gain
    I2_fft *= SFC_gain
    Q2_fft *= SFC_gain

    I1_fft[0] = Q1_fft[0] = I2_fft[0] = Q2_fft[0] = 0

    I1_amp = np.abs(I1_fft)
    I1_phase = np.degrees(np.angle(I1_fft))
    Q1_amp = np.abs(Q1_fft)
    Q1_phase = np.degrees(np.angle(Q1_fft))
    I2_amp = np.abs(I2_fft)
    I2_phase = np.degrees(np.angle(I2_fft))
    Q2_amp = np.abs(Q2_fft)
    Q2_phase = np.degrees(np.angle(Q2_fft))

    Rx1 = I1_amp * np.exp(1j * np.radians(I1_phase)) + Q1_amp * np.exp(1j * np.radians(Q1_phase))
    Rx2 = I2_amp * np.exp(1j * np.radians(I2_phase)) + Q2_amp * np.exp(1j * np.radians(Q2_phase))

    Rx1_amp = np.abs(Rx1)
    Rx2_amp = np.abs(Rx2)

    cfar_detection_Rx1, cfar_threshold_Rx1, _ = ca_cfar_detector(Rx1_amp, num_training_cells, num_guard_cells, threshold_factor)
    cfar_detection_Rx2, cfar_threshold_Rx2, _ = ca_cfar_detector(Rx2_amp, num_training_cells, num_guard_cells, threshold_factor)

    # Calculate detected distances and angles for Rx1
    detected_distances_Rx1 = np.where(cfar_detection_Rx1)[0] * RANGE_BIN_SIZE
    detected_angles_Rx1 = angles[cfar_detection_Rx1]

    # Calculate detected distances and angles for Rx2
    detected_distances_Rx2 = np.where(cfar_detection_Rx2)[0] * RANGE_BIN_SIZE
    detected_angles_Rx2 = angles[cfar_detection_Rx2]

    # Call the plotting functions
    plot_polar_detections(ax_polar, detected_distances_Rx1, detected_angles_Rx1, detected_distances_Rx2, detected_angles_Rx2, MAX_DIST)
    plot_cartesian_detections(ax_cartesian, Rx1_amp, Rx2_amp, cfar_detection_Rx1, cfar_detection_Rx2, cfar_threshold_Rx1, cfar_threshold_Rx2, detected_distances_Rx1, detected_distances_Rx2, range_vector)

# Create animations for each figure separately
num_frames = 25
ani_polar = FuncAnimation(fig_polar, update, frames=range(num_frames), interval=250)
ani_cartesian = FuncAnimation(fig_cartesian, update, frames=range(num_frames), interval=250)

# # Display animations in Jupyter Notebook
from IPython.display import HTML
display(HTML(ani_polar.to_jshtml()))
display(HTML(ani_cartesian.to_jshtml()))